In [1]:
from ckonlpy.tag import Twitter
import pickle
import re
import sys
from gensim.models import TfidfModel
from gensim.models import Word2Vec
from gensim.corpora import Dictionary
from pprint import pprint
from collections import Counter
import numpy as np
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.decomposition import LatentDirichletAllocation
import mglearn
from pprint import pprint
from ckonlpy.tag import Twitter
import numpy as np
import gc
import copy
import pandas as pd

class Social_analysis():
    
    non_bmp_map = dict.fromkeys(range(0x10000, sys.maxunicode + 1), 0xfffd)

    def __init__(self):
        self.twitter = Twitter()
    
    def DB_to_table(self, DBname='intake', keyword='intake'):
        import pymssql
        import pandas.io.sql as pdsql
        import pandas as pd
        self.query = \
        """
        SELECT user_id, created_at, main_text, hashtags, comments, likes, current_url FROM instaPost WHERE keyword = '{}'
        """.format(keyword)
        conn = pymssql.connect("intakedb.c63elkxbiwfc.us-east-2.rds.amazonaws.com:1433", "gh", "ghintake", DBname)
        df = pdsql.read_sql_query(self.query, con=conn)
        # df['main_text'] = df.main_text.apply(lambda x: x.replace('#',' ').translate(self.non_bmp_map))
        # df['created_at'] = df.created_at.apply(lambda x: x.strftime("%Y-%m-%d %H:%M:%S"))
        conn.close()
        self.raw_data = df.as_matrix()        
    
    def pickle_to_table(self, filename):
        with open(filename, 'rb') as f:
            data = pickle.load(f)
        data = data[1:]
        for idx, i in enumerate(data):
            data[idx][2] = i[2].replace('#', ' ').translate(self.non_bmp_map)
            data[idx][3] = '/'.join(i[3])
            data[idx][4] = '/'.join(i[4])
        self.raw_data = np.array(data)
  
    def hashtags_split(self, hashtags):        
        hashtags_split = []
        for i in hashtags:
            hashtags_split.append(i.split('/'))
        
        hashtags_list = []
        
        for i in hashtags_split:
            temp = []
            for j in i:
                if self.isHangul(j):
                    t_hashtags = j.translate(self.non_bmp_map)
                    temp.append(t_hashtags)
            hashtags_list.append(temp)
        self.hashtags_list = hashtags_list
        
        return hashtags_list
                    
    def add_keyword_dic(self, keyword_list, tag='Noun'):
        for i in keyword_list:
            if type(i) == tuple:
                self.twitter.add_dictionary(i[0], i[1])
            else:
                self.twitter.add_dictionary(i, tag)
        
    def morph_pos(self, text_list, exception_list = ['맛', '밥', '물', '몸']):
        
        morph_list = []
        noun_list = []
        adj_list = []
        verb_list = []
        nav_list = []
        
        for j in text_list:
            parsed = self.twitter.pos(j)
            temp = []
            n_temp = []
            adj_temp = []
            verb_temp = []
            nav_temp = []
            
            for i in parsed:
                if self.isHangul(i[0]):
                    if ((len(i[0]) > 1) or (i[0] in exception_list)):
                        temp.append(i)
                        if i[1] == 'Noun':
                            n_temp.append(i[0])
                            nav_temp.append(i[0])
                        elif i[1] == 'Verb':
                            adj_temp.append(i[0])
                            nav_temp.append(i[0])
                        elif i[1] == 'Adjective':
                            verb_temp.append(i[0])
                            nav_temp.append(i[0])
                    else:
                        print('{} 제외'.format(i[0]))
                else: print('{} 한글이 아님.'.format(i[0]))
            

            morph_list.append(temp)
            noun_list.append(n_temp)
            adj_list.append(adj_temp)
            verb_list.append(verb_temp)
            nav_list.append(nav_temp)

        return morph_list, nav_list, noun_list, adj_list, verb_list


    
    def pos_extractor(self, parsed):

        noun_list = []
        adj_list = []
        verb_list = []
        nav_list = []
        for i in parsed:            
            n_temp = []
            adj_temp = []
            verb_temp = []
            nav_temp = []
            if self.isHangul(i[0]):
                if ((len(i[0]) > 1) or (i[0] in exception_list)):
                    if i[1] == 'Noun':
                        n_temp.append(i[0])
                        nav_temp.append(i[0])
                    elif i[1] == 'Verb':
                        adj_temp.append(i[0])
                        nav_temp.append(i[0])
                    elif i[1] == 'Adjective':
                        verb_temp.append(i[0])
                        nav_temp.append(i[0])
                else:
                    print('{} 제외'.format(i[0]))
            else: print('{} 한글이 아님.'.format(i[0]))
            
            noun_list.append(n_temp)
            adj_list.append(adj_temp)
            verb_list.append(verb_temp)
            nav_list.append(nav_temp)
            
        return nav_list, noun_list, adj_list, verb_list

    
    
    def merge_list(self, tokenized_list):
        return [j for i in tokenized_list for j in i]

    
    def join_list(self, tokenized_list):
        joined_list = []
        for idx, i in enumerate(tokenized_list):
            joined_list.append(" ".join(i))
        return joined_list
 
    def split_list(self, untokenized_list):
        hashtag_splited = []
        for idx, i in enumerate(untokenized):
            hashtag_splited.append(i.split('/'))
            return hastag_splited
        
    def join_underbar(self, morph_list):

        all_list = []
        post_list=[]
        for i in morph_list:
            for j in i:
                post_list.append(j[0]+'_'+j[1])
            all_list.append([(' , ').join(post_list)])
            post_list=[] 
        all_list=np.array(all_list)
        
        return all_list

    def word_substitute(self, dataset, sublist):
        dataset = copy.deepcopy(dataset)
        sub_book = dict()
        for i in sublist:
            for j in i['sub_words']:
                sub_book[j] = i['main']
        gc.collect()
        for n, i in enumerate(dataset):
            dataset[n] = [sub_book.get(item,item) for item in i]

        del sub_book
        gc.collect()

        return dataset
    
    def word_delete(self, dataset, del_list):
        dataset = copy.deepcopy(dataset)

        for n, line in enumerate(dataset):
             dataset[n] = [i for i in line if i not in del_list]

        return dataset

    
    def isHangul(self, text):
        encText = text
        hanCount = len(re.findall(u'[\u3130-\u318F\uAC00-\uD7A3]+', encText))
        return hanCount > 0
    
    def convert_list(self, *tokenized_list):
        input_length = len(tokenized_list)
        lists = [[] for i in range(input_length)]

        for idx, li in enumerate(tokenized_list):
            for j in li:
                lists[idx].append(['/'.join(j)])

        converted_array = np.array(lists[0])
        for idx in range(input_length):
            try:
                converted_array = np.concatenate((converted_array, lists[idx + 1]), axis=1)
            except Exception as e:
                print(e,'끝')

        return converted_array

    def make_df(self, converted_array):
        df = pd.DataFrame(np.hstack((intake.raw_data[:,:3], converted_array, intake.raw_data[:, 3:])), index=None)
        return df
    
    # 키워드 리스트 중 하나라도 있는 경우
    def word_check_or(self, text, keywords):
        if any(word in text for word in keywords): return True
        else: return False

    # 키워드 리스트에 있는 단어가 모두 있는 경우
    def word_check_and(self, text, keywords):
        if all(word in text for word in keywords): return True
        else: return False


    def word_check(self, method='and', keywords=[], df = None, column_name = None, filter_TF=True):
        if method == 'and':
            df['flag'] = df[column_name].apply(lambda x: self.word_check_and(x, keywords))
            return df[df.flag==filter_TF]

        if method == 'or':
            df['flag'] = df[column_name].apply(lambda x: self.word_check_or(x, keywords))
            return df[df.flag==filter_TF]


class SB_Word2Vec():    
    
    def __init__(self, morph_list):
        self.dct = Dictionary(morph_list)
        self.corpus = [self.dct.doc2bow(line) for line in morph_list]
        self.build_Word2Vec(morph_list)
    
    def make_Word2Vec(self, morph_list, size=50, window=2, min_count=10, iteration=100):
        self.em = Word2Vec(morph_list, size=size, window=window, min_count=min_count, iter=iteration)
        self.em_vocab = list(self.em.wv.vocab.keys())
        self.em_vocab_dic = {word:idx for idx, word in enumerate(self.em_vocab)}

    def make_Word2Sen_matrix(self): 
        vocab_size = len(self.em_vocab)
        self.sen_matrix = np.zeros((len(self.corpus), vocab_size))
        for idx, row in enumerate(self.sen_matrix):
            for idx2, frequency in self.corpus[idx]:
                    if self.dct[idx2] in self.em_vocab:
                        self.sen_matrix[idx][self.em_vocab_dic[self.dct[idx2]]] = frequency                
        self.sim_matrix = np.zeros((vocab_size, vocab_size))
        for idx, w1 in enumerate(self.em_vocab):
            for idx2, w2 in enumerate(self.em_vocab):
                self.sim_matrix[idx][idx2] =  self.em.wv.similarity(w1, w2)

        self.word2sen_matrix = np.dot(self.sim_matrix, np.transpose(self.sen_matrix))

        return self.word2sen_matrix

    def get_sim_sen(self, keyword, main_text, number=1):
        self.sim_sen_index = np.argsort(self.word2sen_matrix[self.em_vocab_dic[keyword]])
        self.most_sim_sen_index = np.argmax(self.word2sen_matrix[self.em_vocab_dic[keyword]])
        index_list = self.sim_sen_index.reshape((-1,)).tolist()
        index_list.reverse()
        
        for idx, i in enumerate(index_list[:number]):
            print(str(idx + 1))
            print(main_text[i])
        return index_list
    
    def build_Word2Vec(self, morph_list):
        self.make_Word2Vec(morph_list)
        self.make_Word2Sen_matrix()
        
        
class SB_LDA():

    def make_lda(self, morph_joined, ntopic=10, learning_method='batch', max_iter=25, random_state=0, n_words=20):        
        self.vect = CountVectorizer(max_features=10000, max_df=.15)
        self.X = self.vect.fit_transform(morph_joined)
        self.lda = LatentDirichletAllocation(n_components=ntopic, learning_method=learning_method, max_iter=max_iter, random_state=random_state)
        self.document_topics = self.lda.fit_transform(self.X)
        self.sorting = np.argsort(self.lda.components_, axis=1)[:, ::-1]
        self.feature_names = np.array(self.vect.get_feature_names())
        mglearn.tools.print_topics(topics=range(ntopic), feature_names=self.feature_names, sorting=self.sorting, topics_per_chunk=5, n_words=n_words)

    def related_doc(self, main_text_list, topic_index, number=10):
        category = np.argsort(self.document_topics[:, topic_index])[::-1]
        related_docs = []
        for i in category[:number]:
            print(i)
            print(main_text_list[i] + ".\n")
            related_docs.append((i, main_text_list[i]))
        return related_docs

class SB_Tfidf():    
    
    def __init__(self, list_morph_merged):
        self.list_morph_merged = list_morph_merged
        self.dct = Dictionary(self.list_morph_merged)
        self.corpus = [self.dct.doc2bow(line) for line in self.list_morph_merged]

    def get_tfidf(self):       
        self.model = TfidfModel(self.corpus)
        self.tfidf = []
        for i in self.corpus:
             self.tfidf.append(sorted(self.model[i], key = lambda x: x[1], reverse=True))
        self.tfidf_hangul = []
        for idx1, i in enumerate(self.tfidf):
            self.tfidf_hangul.append([(self.dct[j[0]], j[1]) for j in i])        
        
        return self.tfidf_hangul
    
def frequency(merged):
    word_count = Counter(merged)
    word_count2 = []
    for i in word_count:
        word_count2.append((i, word_count[i]))
    word_count2 = sorted(word_count2, key=lambda x: x[1], reverse = True)
    return word_count2

C:\Users\abys\Anaconda3\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


In [2]:
intake = Social_analysis()

In [4]:
labnosh = Social_analysis()

## DB에서 불러온 데이터를 Social_analysis 인스턴스에 등록해도  되고,  그냥 그 데이터로 앞으로 진행해도 된다. 일단 튜토리얼은 pickle 데이터로 진행하기 때문에 아래 함수를 실행하면 intake.row_data 에 저장이 된다. 이 놈은 DB에 들어간 놈이 비슷하게 생긴 놈이다.

In [3]:
intake.pickle_to_table('Data/intake_list.txt')

In [6]:
labnosh.pickle_to_table('Data/labnosh_list.txt')

In [ ]:
intake.DB_to_table("intake", "intake")

## 포함어, 제외어 설정해서 df 를 바꿀 수 있다.
## 파리미터는
## method='and', keywords=[], df = None, column_name = None, filter_TF=True
## method는 and/or 인데 and는 단어들이 전부다 포함되어야하고, or은 하나라도 있으면 된다.
## keywords 는 키워드
## df_name에는 데이터프레임
## column_name 참조할 컬럼
## True 는 만족하는 모든 것, False 그것 뺀 나머지

In [19]:
df = pd.DataFrame(intake.raw_data, columns=['user_id', 'created_at', 'main_text', 'hashtags', 'comments', 'likes', 'current_url'])

In [20]:
df_new = intake.word_check('or', ['흡기', '배기','도어락'], df, 'hashtags', False)
df_new = intake.word_check('or', ['intakefoods'], df_new, 'user_id', False)

C:\Users\abys\Anaconda3\lib\site-packages\ipykernel_launcher.py:252: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


In [16]:
df_new.head(100)

user_id                created_at  \
0        lora.study  2018-07-03T23:57:47.000Z   
1          1122_asm  2018-07-02T01:08:57.000Z   
2       makemysugar  2018-07-05T13:13:05.000Z   
3     oasis_jaeyoon  2018-06-28T01:59:52.000Z   
4          khjhmom_  2018-07-04T11:01:04.000Z   
5          leeminwk  2018-06-12T11:05:21.000Z   
6             vveun  2018-06-13T13:26:21.000Z   
7      _si1ver_star  2018-01-14T12:30:54.000Z   
8    kyu_ri_the_one  2018-04-21T12:56:13.000Z   
9      untactmarket  2018-07-06T07:46:02.000Z   
10          155__44  2018-07-06T04:32:10.000Z   
11        jiseung86  2018-07-06T03:35:06.000Z   
12       monicain25  2018-07-06T02:42:37.000Z   
13      suni_suni27  2018-07-06T01:00:37.000Z   
14       soono_7473  2018-07-05T23:37:47.000Z   
15       berry_eats  2018-07-05T21:41:08.000Z   
16           787_92  2018-07-05T17:12:46.000Z   
17         _0917_hj  2018-07-05T16:01:38.000Z   
18       berry_eats  2018-07-05T13:48:33.000Z   
19           09_21g  2018-07-05T13:42:55.000Z   
20         diet.goo  2018-07-05T11:59:17.000Z   
21      june_rollas  2018-07-05T11:42:01.000Z   
22       _eunjishin  2018-07-05T07:25:43.000Z   
23         bbasha12  2018-07-05T05:05:08.000Z   
24        lee.mihwa  2018-07-05T02:53:54.000Z   
25    jiyoungkim516  2018-07-05T00:33:01.000Z   
26    marina_dieter  2018-07-05T00:02:26.000Z   
27    purplerain_99  2018-07-04T14:15:01.000Z   
28       mominine_h  2018-07-04T12:35:00.000Z   
29     hoonseokjeon  2018-07-04T07:52:49.000Z   
..              ...                       ...   
70     sunnykimhehe  2018-06-27T15:08:25.000Z   
71       hyounii_26  2018-06-27T13:15:29.000Z   
72       happysijoo  2018-06-27T13:12:40.000Z   
73    kyunghee.lee1  2018-06-27T12:54:56.000Z   
74    hyelth_tagram  2018-06-27T12:49:37.000Z   
75       nanahollic  2018-06-27T11:50:19.000Z   
76       dlskdgml01  2018-06-27T10:42:43.000Z   
77        binandjun  2018-06-27T08:23:32.000Z   
78     dameulstudio  2018-06-27T07:17:04.000Z   
79        caris_pak  2018-06-27T06:24:17.000Z   
80     hwayoung2000  2018-06-27T04:47:49.000Z   
82          zonemad  2018-06-27T03:13:40.000Z   
83          so.y_94  2018-06-27T02:59:35.000Z   
84          hssun24  2018-06-27T01:09:27.000Z   
85        sso_byeol  2018-06-26T19:33:43.000Z   
86          zonemad  2018-06-26T19:03:59.000Z   
87       sun.a.1376  2018-06-26T15:51:34.000Z   
88     d.myday_1027  2018-06-26T12:53:01.000Z   
89   sangmin_kim411  2018-06-26T10:45:27.000Z   
90   hahhaya_modern  2018-06-26T04:22:27.000Z   
91   lliichachaiill  2018-06-26T04:19:14.000Z   
92         0harace0  2018-06-26T02:01:01.000Z   
93      sallydieter  2018-06-26T01:39:02.000Z   
94       suyeonvovo  2018-06-26T01:35:11.000Z   
95          chyumuk  2018-06-26T00:45:17.000Z   
96         hoya8929  2018-06-26T00:40:52.000Z   
97         zera_fam  2018-06-25T23:09:58.000Z   
98     d.myday_1027  2018-06-25T13:51:23.000Z   
99          rovvkzv  2018-06-25T10:31:34.000Z   
100        lulie___  2018-06-25T00:35:06.000Z   

                                             main_text  \
0    lora.study 아침식사 죽 모닝죽 단호박 인테이크\n.\n몇년째 먹는 모닝죽\...   
1    1122_asm.\n바쁜아침 식사대용으로 마시고 있는,\n가벼운 한끼  인테이크  ...   
2    makemysugar.\n아침에 귀찮아서 간편하게 귀리우유 한 잔�!\n고소~~하니...   
3    oasis_jaeyoon오늘 아침은 짜먹는 죽. 어제 모임에서 선물로 받았다. 세상...   
4    khjhmom_몸을 좀비워야할시기�\n.\n.\n.\n 육아한답시고 너무먹어ㅎ ㅎ\...   
5    leeminwk차에서 라디오 듣다 문자 보냈는데  인테이크 상품권 받음.\n요즘은 ...   
6                                  vveun나이제 술 안먹어�� 정말   
7    _si1ver_star1일1식으로 딱이야 넘 맛남( ๑॔˃̶◡ ˂̶๑॓)◞♡\n 인...   
8    kyu_ri_the_one고소하고 맛있는 175kal 한 끼 식사�\n.\n.\n....   
9    untactmarket-\n지금 샐러드를 사면\n럭키 복권이 따라와요!\n긁으면 대...   
10   155__44180706☁️\n 점심  식단 �\n▪️카레(곤약현미밥&버터치킨커리)...   
11   jiseung86 VWUNION\n VOGTLAND\n 광명 놀러오세요\n 골프\n...   
12   monicain25 인테이크 INTAKE 모닝귀리 밀스칩 Mealschip 미래지향...   
13   suni_suni27 주원공복운동 3세트\n 빨랫줄운동 100\n 아침\n 인테이크...   
14       soono_7473 고농축단백질  인테이크  덴마크  밀스드링크딸기�  화장실ㄱㄱ   
15   berry_eats간식챱챱�\n인테이크 [밀스 프레시모닝 1.0]\n\n

In [18]:
df_new.describe()

user_id                created_at  \
count          4957                      4957   
unique         2968                      4926   
top     gweonyeonho  2017-10-10T03:01:45.000Z   
freq            113                         2   

                                                main_text  \
count                                                4957   
unique                                               4923   
top     songdorunningcrew_\n@songdorunningcrew x @inta...   
freq                                                    8   

                                                 hashtags comments likes  \
count                                                4957     4957  4957   
unique                                               4678     3070   508   
top     도어락/폭스바겐골프/도색/카스타그램/튜닝/자동차/자동차그램🚘/투스카니/스파크/인테이...                  
freq                                                   30     1878   893   

                                              current_url   flag  
count                                                4957   4957  
unique                                               4926      1  
top     https://www.instagram.com/p/BVbuL7Rjuap/?hl=ko...  False  
freq                                                    2   4957

In [45]:
intake.modified = df_new.as_matrix()

## 형태소 분석에 꼭 포함하고 싶은 단어를 추가한다. 기본적으로는 hashtag들을 noun으로 추가한다. 여기서 해쉬태그 중에 포함하고 싶지 않은 것을 빼는 것을 추천한다.

In [49]:
intake.hashtag_splited = intake.hashtags_split(intake.modified[:, 3])
print(np.shape(intake.hashtag_splited))
print(intake.hashtag_splited[0])

(5235,)
['아침식사', '죽', '모닝죽', '단호박', '인테이크', '맛스타그램', '먹스타그램', '식사대용', '다이어트', '두통', '좋아요반사', '맛집', '간편식', '아점', '아픔', '선팔은맞팔', '맛스타', '선팔', '맞팔', '먹스타', '음식', '푸드스타그램', '좋반']


In [4]:
labnosh.hashtag_splited = labnosh.hashtags_split(labnosh.raw_data[:, 3])
print(np.shape(labnosh.hashtag_splited))
print(labnosh.hashtag_splited[0])

NameError: name 'labnosh' is not defined

## intake.add_dic_keyword() 함수는 1차원 list를 받는다.
## 데이터의 형태는 ['단어', '단어', '단어'] or [('단어', Tag), ('단어', Tag)]
## Tag는 'Noun', 'Verb', 'Adjective' 등이 있다.

In [50]:
intake.hashtag_merged = intake.merge_list(intake.hashtag_splited)

intake.add_keyword_dic(intake.hashtag_splited)

In [ ]:
labnosh.hashtag_merged = labnosh.merge_list(labnosh.hashtag_splited)

labnosh.add_keyword_dic(labnosh.hashtag_splited)

## 형태소 분석을 진행한다. 한글자는 제외시키는데 혹시 필요하다고 판단되는 글자는 exception_list 파라미터에 리스트로 넣어주면 된다.

In [51]:
intake.morph_list, intake.nav_list, intake.noun_list, intake.adj_list, intake.verb_list= intake.morph_pos(intake.modified[:, 2], exception_list=['맛', '밥', '물', '몸', '죽'])

lora 한글이 아님.
. 한글이 아님.
study 한글이 아님.
. 한글이 아님.
몇 제외
년 제외
째 제외
먹 제외
는 제외
엔 제외
하 제외
고 제외
도 제외
데 제외
면 제외
� 한글이 아님.
가 제외
데 제외
.. 한글이 아님.
다 제외
랑 제외
가 제외
오 제외
� 한글이 아님.
1122 한글이 아님.
_ 한글이 아님.
asm 한글이 아님.
. 한글이 아님.
고 제외
, 한글이 아님.
. 한글이 아님.
먹 제외
을 제외
수 제외
수 제외
요 제외
! 한글이 아님.
는 제외
일 제외
요 제외
. 한글이 아님.
감 제외
있 제외
게 제외
! 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
makemysugar 한글이 아님.
. 한글이 아님.
한 제외
잔 제외
� 한글이 아님.
! 한글이 아님.
~~ 한글이 아님.
먹 제외
는 제외
것 제외
가 제외
틈 제외
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
oats 한글이 아님.
oatmeal 한글이 아님.
oasis 한글이 아님.
_ 한글이 아님.
jaeyoon 한글이 아님.
짜 제외
. 한글이 아님.
로 제외
다 제외
. 한글이 아님.
이 제외
. 한글이 아님.
khjhmom 한글이 아님.
_ 한글이 아님.
을 제외
워 제외
시 제외
기 제외
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
ㅎ 제외
leeminwk 한글이 아님.
차 제외
받 제외
음 제외
. 한글이 아님.
은 제외
만 제외
한 제외
질 제외
vveun 한글이 아님.
제 제외
술 제외
안 제외
�� 한글이 아님.
_ 한글이 아님.
si 한글이 아님.
1 한글이 아님.
ver 한글이 아님.
_ 한글이 아님.
star 한글이 아님.
1 한글이 아님.
일 제외
1 한글이 아님.
식 제외
딱 제외
넘 제외
( 한글이 아님.
๑॔˃̶◡ 한글이 아님.
˂̶๑॓ 한글이 아님.
) 한글이 아님.
◞♡ 한글이 아님.
kyu 한글이 아님.
_ 한글이 아님

happysijoo 한글이 아님.
- 한글이 아님.
- 한글이 아님.
- 한글이 아님.
즈 제외
니 제외
들 제외
이 제외
와 제외
어 제외
! 한글이 아님.
들 제외
이 제외
어 제외
! 한글이 아님.
감 제외
다 제외
? 한글이 아님.
응 제외
! 한글이 아님.
❤️ 한글이 아님.
- 한글이 아님.
도 제외
던 제외
들 제외
뿐 제외
❤️ 한글이 아님.
가 제외
더 제외
갑 제외
! 한글이 아님.
~ 한글이 아님.
앞 제외
가 제외
될 제외
때 제외
갚 제외
�� 한글이 아님.
- 한글이 아님.
( 한글이 아님.
@choneeeeee 한글이 아님.
) 한글이 아님.
( 한글이 아님.
@0harace0 한글이 아님.
) 한글이 아님.
( 한글이 아님.
@peechypeechy 한글이 아님.
) 한글이 아님.
————————————— 한글이 아님.
( 한글이 아님.
, 한글이 아님.
, 한글이 아님.
@lhs11177 한글이 아님.
) 한글이 아님.
( 한글이 아님.
@runner_g100 한글이 아님.
) 한글이 아님.
—————————————— 한글이 아님.
( 한글이 아님.
@naked_hongs 한글이 아님.
) 한글이 아님.
광 제외
래 제외
( 한글이 아님.
, 한글이 아님.
@luciano_kwangrae 한글이 아님.
) 한글이 아님.
( 한글이 아님.
, 한글이 아님.
@reason_1_ 한글이 아님.
) 한글이 아님.
( 한글이 아님.
, 한글이 아님.
@8282yoon 한글이 아님.
) 한글이 아님.
—————————————— 한글이 아님.
- 한글이 아님.
( 한글이 아님.
, 한글이 아님.
짐 제외
@wi_kay 한글이 아님.
) 한글이 아님.
, 한글이 아님.
( 한글이 아님.
@hanxxdam 한글이 아님.
@hongxxsom 한글이 아님.
) 한글이 아님.
- 한글이 아님.
runner 한글이 아님.
running 한글이 아님.
runstagram 한글이 아님.
kyunghee 한글이 아님.
. 한글이 아님.
lee 한글이 아님.


kimmin 한글이 아님.
___ 한글이 아님.
j 한글이 아님.
10 한글이 아님.
k 한글이 아님.
런 제외
자 제외
립 제외
3 한글이 아님.
차 제외
10 한글이 아님.
k 한글이 아님.
로 제외
뛰 제외
었 제외
다 제외
.. 한글이 아님.
분 제외
들 제외
이 제외
뛰 제외
며 제외
신 제외
에 제외
이 제외
였 제외
다 제외
. 한글이 아님.
전 제외
선 제외
도 제외
고 제외
가 제외
는 제외
에 제외
!! 한글이 아님.
후 제외
을 제외
을 제외
당 제외
!! 한글이 아님.
도 제외
고 제외
10 한글이 아님.
할 제외
수 제외
과 제외
런 제외
님 제외
! 한글이 아님.
한 제외
선 제외
엉 제외
♥ 한글이 아님.
해 제외
( 한글이 아님.
@choneeeeee 한글이 아님.
) 한글이 아님.
( 한글이 아님.
@0harace0 한글이 아님.
) 한글이 아님.
( 한글이 아님.
@peechypeechy 한글이 아님.
) 한글이 아님.
————————————— 한글이 아님.
( 한글이 아님.
, 한글이 아님.
, 한글이 아님.
@lhs11177 한글이 아님.
) 한글이 아님.
( 한글이 아님.
@runner_g100 한글이 아님.
) 한글이 아님.
——————————— 한글이 아님.
- 한글이 아님.
———— 한글이 아님.
( 한글이 아님.
@naked_hongs 한글이 아님.
) 한글이 아님.
광 제외
래 제외
( 한글이 아님.
, 한글이 아님.
@luciano_kwangrae 한글이 아님.
) 한글이 아님.
( 한글이 아님.
, 한글이 아님.
@reason_1_ 한글이 아님.
) 한글이 아님.
( 한글이 아님.
, 한글이 아님.
@8282yoon 한글이 아님.
) 한글이 아님.
—————————————— 한글이 아님.
- 한글이 아님.
( 한글이 아님.
, 한글이 아님.
짐 제외
@wi_kay 한글이 아님.
) 한글이 아님.
, 한글이 아님.
( 한글이 아님.
@hanxxdam 한글이 아님.
@hongxxsom 한글이 아님.
) 한글이 아님

h.beagle.diet 한글이 아님.
18 한글이 아님.
. 한글이 아님.
06 한글이 아님.
. 한글이 아님.
12 한글이 아님.
화 제외
60 한글이 아님.
g 한글이 아님.
( 한글이 아님.
20 한글이 아님.
g 한글이 아님.
+ 한글이 아님.
40 한글이 아님.
g 한글이 아님.
) 한글이 아님.
1 한글이 아님.
/ 한글이 아님.
2 한글이 아님.
개 제외
, 한글이 아님.
� 한글이 아님.
1 한글이 아님.
개 제외
, 한글이 아님.
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
176 한글이 아님.
g 한글이 아님.
, 한글이 아님.
� 한글이 아님.
1 한글이 아님.
개 제외
, 한글이 아님.
� 한글이 아님.
3 한글이 아님.
개 제외
( 한글이 아님.
2 한글이 아님.
개 제외
, 한글이 아님.
만 제외
1 한글이 아님.
개 제외
) 한글이 아님.
. 한글이 아님.
한 제외
에 제외
음 제외
! 한글이 아님.
1 한글이 아님.
병 제외
, 한글이 아님.
고 제외
쉬 제외
을 제외
때 제외
. 한글이 아님.
쌤 제외
를 제외
샀 제외
음 제외
안 제외
먹 제외
을 제외
꺼 제외
데 제외
.. 한글이 아님.
내 제외
손 제외
은 제외
로 제외
� 한글이 아님.
� 한글이 아님.
. 한글이 아님.
2 한글이 아님.
개 제외
, 한글이 아님.
. 한글이 아님.
업 제외
, 한글이 아님.
, 한글이 아님.
, 한글이 아님.
. 한글이 아님.
30 한글이 아님.
분 제외
뒤 제외
1 한글이 아님.
잔 제외
3 한글이 아님.
뒤 제외
3 한글이 아님.
. 한글이 아님.
거 제외
날 제외
� 한글이 아님.
� 한글이 아님.
� 한글이 아님.
. 한글이 아님.
이 제외
잘 제외
다 제외
.. 한글이 아님.
에 제외
� 한글이 아님.
. 한글이 아님.
diet 한글이 아님.
myprotein 한글이 아님.
과 제외
intake 한글이 아님.
와 제외
F 한글이 아님.
7 한글이 아님.
TJ 한글이 아님.
- 한글이 아님.
R 한글이 아님.
2 한글이

obrightoo 한글이 아님.
뭘 제외
씹 제외
을 제외
수 제외
가 제외
..... 한글이 아님.
ㅜ 제외
lifestyle 한글이 아님.
snu 한글이 아님.
exam 한글이 아님.
eat 한글이 아님.
food 한글이 아님.
foodstagram 한글이 아님.
yum 한글이 아님.
eatclean 한글이 아님.
plantbased 한글이 아님.
vegan 한글이 아님.
chocolate 한글이 아님.
meal 한글이 아님.
チョコレート 한글이 아님.
試験 한글이 아님.
breakfast 한글이 아님.
. 한글이 아님.
jaym 한글이 아님.
2018 한글이 아님.
면 제외
19 한글이 아님.
일 제외
선 제외
식 제외
. 한글이 아님.
3 한글이 아님.
. 한글이 아님.
0 한글이 아님.
그 제외
. 한글이 아님.
말 제외
이 제외
. 한글이 아님.
첨 제외
에 제외
먹 제외
을 제외
땐 제외
만 제외
한 제외
것 제외
하 제외
게 제외
한 제외
하 제외
는 제외
? 한글이 아님.
hyunwoorimyy 한글이 아님.
인 제외
!!!!!! 한글이 아님.
ㅋ 제외
는 제외
니 제외
몫 제외
... 한글이 아님.
raksik.co.kr 한글이 아님.
게 제외
한 제외
끼 제외
! 한글이 아님.
⠀ 한글이 아님.
. 한글이 아님.
⠀ 한글이 아님.
" 한글이 아님.
진 제외
, 한글이 아님.
" 한글이 아님.
OR 한글이 아님.
" 한글이 아님.
59243 한글이 아님.
" 한글이 아님.
을 제외
요 제외
! 한글이 아님.
⠀ 한글이 아님.
. 한글이 아님.
⠀ 한글이 아님.
d 한글이 아님.
. 한글이 아님.
myday 한글이 아님.
_ 한글이 아님.
1027 한글이 아님.
� 한글이 아님.
2018 한글이 아님.
. 한글이 아님.
06 한글이 아님.
. 한글이 아님.
18 한글이 아님.
� 한글이 아님.
: 한글이 아님.
: 한글이 아님.
: 한글이 아님.
, 한글이 아님.
: 한글이 아님.
, 한글이 아님.
1 한글이 아님.
개 제외
, 한글이 아님.


...

intakefoods 한글이 아님.
6 한글이 아님.
콩 제외
적 제외
에 제외
가 제외
주 제외
신 제외
이 제외
건 제외
왜 제외
일 제외
까 제외
요 제외
~ 한글이 아님.
ᆞ 한글이 아님.
를 제외
주 제외
신 제외
@kms201031 한글이 아님.
님 제외
! 한글이 아님.
ᆞ 한글이 아님.
. 한글이 아님.
는 제외
는 제외
분 제외
, 한글이 아님.
이 제외
신 제외
분 제외
들 제외
을 제외
위 제외
한 제외
을 제외
다 제외
! 한글이 아님.
. 한글이 아님.
는 제외
>< 한글이 아님.
. 한글이 아님.
intakefoods 한글이 아님.
가 제외
깔 제외
끄 제외
?? 한글이 아님.
. 한글이 아님.
를 제외
주 제외
신 제외
@chilli_k 한글이 아님.
님 제외
!! 한글이 아님.
・・・ 한글이 아님.
꼭 제외
은 제외
서 제외
의 제외
를 제외
한 제외
들 제외
, 한글이 아님.
로 제외
� 한글이 아님.
. 한글이 아님.
는 제외
는 제외
분 제외
, 한글이 아님.
이 제외
신 제외
분 제외
들 제외
을 제외
위 제외
한 제외
을 제외
다 제외
! 한글이 아님.
. 한글이 아님.
는 제외
>< 한글이 아님.
. 한글이 아님.
de 한글이 아님.
_ 한글이 아님.
jooey 한글이 아님.
. 한글이 아님.
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
intakefoods 한글이 아님.
은 제외
!! 한글이 아님.
・・・ 한글이 아님.
�� 한글이 아님.
. 한글이 아님.
를 제외
주 제외
신 제외
@green_maru 한글이 아님.
님 제외
! 한글이 아님.
. 한글이 아님.
. 한글이 아님.
는 제외
는 제외
분 제외
, 한글이 아님.
이 제외
신 제외
분 제외
들 제외
을 제외
위 제외
한 제외
을 제외
다 제외
! 한글이 아님.
. 한글이 아님.
는 제외
>< 한글이 아님.
. 한글이 아님.
hayjooo 한글이 아님.
라 제외
때 제외
로 제외
딱 제외
�� 한글이 아님.
* 한글이 아님.
본 제외
피 제외
었 제외


yoo 한글이 아님.
. 한글이 아님.
hana 한글이 아님.
517 한글이 아님.
. 한글이 아님.
� 한글이 아님.
Diet 한글이 아님.
+ 한글이 아님.
484 한글이 아님.
� 한글이 아님.
20151118 한글이 아님.
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
➡️ 한글이 아님.
1 한글이 아님.
/ 한글이 아님.
2 한글이 아님.
1 한글이 아님.
1 한글이 아님.
컵 제외
3 한글이 아님.
1 한글이 아님.
컵 제외
➡️ 한글이 아님.
& 한글이 아님.
& 한글이 아님.
➡️ 한글이 아님.
색 제외
이 제외
뿐 제외
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
가 제외
추 제외
운 제외
것 제외
요 제외
저 제외
만 제외
ㅠ 제외
기 제외
어 제외
:) 한글이 아님.
2 한글이 아님.
되 제외
서 제외
! 한글이 아님.
표 제외
랑 제외
다 제외
은 제외
! 한글이 아님.
잘 제외
제 제외
먹 제외
로 제외
:) 한글이 아님.
. 한글이 아님.
되 제외
! 한글이 아님.
. 한글이 아님.
가 제외
며 제외
..! 한글이 아님.
. 한글이 아님.
어 제외
� 한글이 아님.
이 제외
를 제외
! 한글이 아님.
가 제외
등 제외
을 제외
줘 제외
요 제외
! 한글이 아님.
. 한글이 아님.
제 제외
가 제외
� 한글이 아님.
님 제외
들 제외
♥️♥️♥️♥️♥️♥️ 한글이 아님.
요 제외
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
ccang 한글이 아님.
diet 한글이 아님.
dietfood 한글이 아님.
DANO 한글이 아님.
_ 한글이 아님.
_ 한글이 아님.
_ 한글이 아님.
�� 한글이 아님.
after 한글이 아님.
_ 한글이 아님.
10 한글이 아님.
y 한글이 아님.
넘 제외
는 제외
intake 한글이 아님.
은 제외
, 한글이 아님.
잘 제외
용 제외
:) 한글이 아님.
� 한글이 아님.
yoo 한글이 아님.
. 한글이 아님.
ha

san 한글이 아님.
_ 한글이 아님.
rim 한글이 아님.
- 한글이 아님.
째 제외
� 한글이 아님.
3 한글이 아님.
일 제외
안 제외
됐 제외
.. 한글이 아님.
의 제외
� 한글이 아님.
intake 한글이 아님.
san 한글이 아님.
_ 한글이 아님.
rim 한글이 아님.
- 한글이 아님.
� 한글이 아님.
적 제외
은 제외
� 한글이 아님.
intake 한글이 아님.
29 한글이 아님.
centimeter 한글이 아님.
[ 한글이 아님.
] 한글이 아님.
서 제외
먹 제외
되 제외
고 제외
, 한글이 아님.
먹 제외
, 한글이 아님.
뒤 제외
. 한글이 아님.
, 한글이 아님.
, 한글이 아님.
를 제외
요 제외
. 한글이 아님.
29 한글이 아님.
CM 한글이 아님.
FOOD 한글이 아님.
의 제외
1 한글이 아님.
위 제외
를 제외
좋 제외
고 제외
. 한글이 아님.
intakefoods 한글이 아님.
causeiam 한글이 아님.
; 한글이 아님.
' 한글이 아님.
내 제외
에 제외
로 제외
' 한글이 아님.
엔 제외
만 제외
한 제외
양 제외
이 제외
이 제외
어 제외
200 한글이 아님.
에 제외
과 제외
을 제외
한 제외
봉 제외
씩 제외
에 제외
.. 한글이 아님.
양 제외
에 제외
서 제외
100 한글이 아님.
에 제외
한 제외
봉 제외
다 제외
; 한글이 아님.
나 제외
나 제외
ㅋ 제외
ㅋ 제외
데 제외
... 한글이 아님.
때 제외
있 제외
음 제외
... 한글이 아님.
,, 한글이 아님.
때 제외
나 제외
지 제외
; 한글이 아님.
, 한글이 아님.
만 제외
.. 한글이 아님.
가 제외
다 제외
youjijiii 한글이 아님.
못 제외
날 제외
주 제외
오 제외
� 한글이 아님.
한 제외
개 제외
70 한글이 아님.
나 제외
적 제외
은 제외
양 제외
Intake 한글이 아님.
yoo 한글이 아님.
. 한글이 아님.
hana 한글이 아님.
517 한글이 아님.
. 한글이 아님.
20150901 한글이 아님.
� 한글이 아님.


yoo 한글이 아님.
. 한글이 아님.
hana 한글이 아님.
517 한글이 아님.
. 한글이 아님.
2015713 한글이 아님.
. 한글이 아님.
with 한글이 아님.
& 한글이 아님.
& 한글이 아님.
& 한글이 아님.
. 한글이 아님.
하 제외
고 제외
왔 제외
�� 한글이 아님.
은 제외
이 제외
고 제외
� 한글이 아님.
제 제외
가 제외
게 제외
은 제외
못 제외
... 한글이 아님.
간 제외
& 한글이 아님.
로 제외
을 제외
서 제외
는 제외
만 제외
이 제외
어 제외
졌 제외
뭐 제외
든 제외
가 제외
�� 한글이 아님.
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
님 제외
들 제외
용 제외
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
diet 한글이 아님.
dietfood 한글이 아님.
dieter 한글이 아님.
�� 한글이 아님.
yoo 한글이 아님.
. 한글이 아님.
hana 한글이 아님.
517 한글이 아님.
. 한글이 아님.
2015712 한글이 아님.
. 한글이 아님.
with 한글이 아님.
& 한글이 아님.
. 한글이 아님.
이 제외
히 제외
과 제외
후 제외
♥️ 한글이 아님.
는 제외
봤 제외
되 제외
서 제외
봤 제외
겠 제외
�� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
. 한글이 아님.
님 제외
들 제외
용 제외
� 한글이 아님.
. 한글이 아님.
. 한글이 아님.
diet 한글이 아님.
dietfood 한글이 아님.
dieter 한글이 아님.
�� 한글이 아님.
yoo 한글이 아님.
. 한글이 아님.
hana 한글이 아님.
517 한글이 아님.
. 한글이 아님.
2015710 한글이 아님.
. 한글이 아님.
with 한글이 아님.
( 한글이 아님.
) 한글이 아님.
& 한글이 아님.
& 한글이 아님.
� 한글이 아님.
15 한글이 아님.
g 한글이 아님.
. 한글이 아님.
. 한글이 아님.
이 제외
히 제외
여 제외
신 제외
나 제외
� 한글이 아님.
불 제외
리 제외
� 한

yo 한글이 아님.
_ 한글이 아님.
mangyo 한글이 아님.
을 제외
샀 제외
다 제외
3 한글이 아님.
나 제외
.. 한글이 아님.
☆ 한글이 아님.
고 제외
한 제외
왜 제외
지 제외
... 한글이 아님.
왜 제외
가 제외
거 제외
지 제외
... 한글이 아님.
1 한글이 아님.
회 제외
량 제외
지 제외
힝 제외
.... 한글이 아님.
도 제외
에 제외
두 제외
야 제외
징 제외
raksik.co.kr 한글이 아님.
용 제외
. 한글이 아님.
raksik 한글이 아님.
rosoul 한글이 아님.
다 제외
튼 제외
줄 제외
알 제외
았 제외
지 제외
? 한글이 아님.
이 제외
? 한글이 아님.
ㅋ 제외
ㅋ 제외
intake 한글이 아님.
diet 한글이 아님.
superfood 한글이 아님.
ju 한글이 아님.
04230206 한글이 아님.
ㅡ 제외
데 제외
고 제외
다 제외
니 제외
기 제외
좋 제외
을 제외
것 제외
요 제외
motion 한글이 아님.
_ 한글이 아님.
in 한글이 아님.
_ 한글이 아님.
motorsportBMC 한글이 아님.
Airfilter 한글이 아님.
, 한글이 아님.
again 한글이 아님.
the 한글이 아님.
official 한글이 아님.
parts 한글이 아님.
for 한글이 아님.
Super 한글이 아님.
trafeo 한글이 아님.
Huracan 한글이 아님.
bmc 한글이 아님.
bmcairfilters 한글이 아님.
mauri 한글이 아님.
WTCC 한글이 아님.
Ferrari 한글이 아님.
Laferrari 한글이 아님.
gt 한글이 아님.
3 한글이 아님.
rs 한글이 아님.
918 한글이 아님.
spyder 한글이 아님.
performance 한글이 아님.
intake 한글이 아님.
tyyli 한글이 아님.
- 한글이 아님.
고 제외
한 제외
네 제외
아 제외
.. 한글이 아님.
이 제외
것 제외
들 제외
� 한글이 아님.
intake 한글이 아님.
heim 한글이 아님.
lifestyle 한글이 아님.
4

In [6]:
intake.nav_list[:2]

[['아침식사',
  '죽',
  '모닝',
  '죽',
  '단호박',
  '테이크',
  '먹는',
  '모닝',
  '죽',
  '아침',
  '바쁘',
  '기도',
  '하고',
  '입맛',
  '없는',
  '요거',
  '하나',
  '아침',
  '뚝딱',
  '맛',
  '여러',
  '종류',
  '있는',
  '맛있는',
  '굳이',
  '고르',
  '단호박',
  '새로',
  '나온',
  '고구마',
  '맛있'],
 ['바쁜',
  '아침',
  '식사',
  '대용',
  '마시',
  '있는',
  '가벼운',
  '테이크',
  '밀스',
  '라이트',
  '간편하게',
  '있고',
  '영양소',
  '까지',
  '챙길',
  '있어',
  '밀스',
  '라이트',
  '덕분',
  '아침',
  '거르',
  '없어',
  '아침',
  '마다',
  '포만',
  '운동하는',
  '직장인',
  '식단',
  '인증',
  '하루',
  '시작',
  '간식',
  '타임',
  '아침',
  '스타',
  '그램',
  '간식',
  '식사',
  '대용',
  '건강',
  '스타',
  '그램',
  '건강',
  '그램',
  '식사',
  '아침식사',
  '아침',
  '스타',
  '그램',
  '맛있다',
  '그램',
  '맛스타',
  '그램']]

In [ ]:
labnosh.morph_list, labnosh.nav_list, labnosh.noun_list, labnosh.adj_list, labnosh.verb_list= labnosh.morph_pos(labnosh.raw_data[:, 2], exception_list=['맛', '밥', '물', '몸', '죽'])

## 빈도분석에는 merge된 list가 필요하다.

In [54]:
intake.nav_merged = intake.merge_list(intake.nav_list)

intake.nav_frequency = frequency(intake.nav_merged)

pprint(intake.nav_frequency)

[('인테이크', 5727),
 ('다이어트', 2167),
 ('밀스', 1490),
 ('아침', 1273),
 ('모닝죽', 1212),
 ('다이어터', 961),
 ('맛', 938),
 ('일상', 769),
 ('다이어트식단', 753),
 ('먹스타그램', 679),
 ('간식', 647),
 ('저녁', 627),
 ('먹어', 568),
 ('먹고', 566),
 ('운동', 562),
 ('오늘', 551),
 ('점심', 541),
 ('식사대용', 529),
 ('너무', 525),
 ('죽', 454),
 ('다이어트그램', 451),
 ('건강', 424),
 ('에서', 423),
 ('식단', 405),
 ('식단일기', 391),
 ('맛스타그램', 389),
 ('데일리', 386),
 ('씨씨앙', 336),
 ('단호박', 335),
 ('고구마', 333),
 ('소통', 331),
 ('우유', 325),
 ('식단조절', 318),
 ('먹기', 318),
 ('후기', 317),
 ('있는', 316),
 ('해서', 316),
 ('챙겨', 315),
 ('아침식사', 312),
 ('물', 303),
 ('밥', 299),
 ('미래식사', 298),
 ('식사', 292),
 ('구매', 291),
 ('먹었', 286),
 ('이벤트', 283),
 ('두유', 280),
 ('하루', 270),
 ('밀스라이트', 268),
 ('견과류', 263),
 ('칼로리', 254),
 ('많은', 252),
 ('입니', 249),
 ('까지', 244),
 ('라이트', 239),
 ('있어', 238),
 ('먹으', 238),
 ('먹는', 236),
 ('하나', 235),
 ('흡기', 233),
 ('시간', 231),
 ('간편식', 230),
 ('단호박죽', 227),
 ('테이크', 224),
 ('제품', 222),
 ('문의', 222),
 ('맞팔', 220),
 ('같은', 218),
 

 ('멸치', 8),
 ('자랑스타그램', 8),
 ('파슬리', 8),
 ('타임', 8),
 ('튜닝카', 8),
 ('사차인치', 8),
 ('없던', 8),
 ('시대', 8),
 ('식이요법', 8),
 ('해보니', 8),
 ('고요', 8),
 ('안해', 8),
 ('건조', 8),
 ('느껴졌', 8),
 ('오피러스', 8),
 ('베리', 8),
 ('신분', 8),
 ('마시니', 8),
 ('느껴', 8),
 ('실장', 8),
 ('않기', 8),
 ('간편히', 8),
 ('겠다', 8),
 ('인체유래유산균', 8),
 ('연말', 8),
 ('엄청난', 8),
 ('빼는', 8),
 ('메이크업', 8),
 ('소환', 8),
 ('절제', 8),
 ('크로스핏', 8),
 ('파주', 8),
 ('11월', 8),
 ('분석', 8),
 ('디젤', 8),
 ('주문해', 8),
 ('나기', 8),
 ('용도', 8),
 ('파이팅', 8),
 ('주행', 8),
 ('홍대', 8),
 ('아시', 8),
 ('물마시는습관', 8),
 ('건강하고', 8),
 ('디퓨저', 8),
 ('뱃살', 8),
 ('챌린', 8),
 ('체중조절용', 8),
 ('맛저', 8),
 ('규칙', 8),
 ('초보자', 8),
 ('업무', 8),
 ('고급', 8),
 ('운동하는주부', 8),
 ('아이간식', 8),
 ('바질씨', 8),
 ('희망', 8),
 ('잭스코코', 8),
 ('약콩', 8),
 ('다이어트영양제', 8),
 ('추석세트', 8),
 ('씨씨모닝', 8),
 ('파워업', 8),
 ('다노한웅녀', 8),
 ('모건블랙', 8),
 ('높였', 8),
 ('빈스파이브', 8),
 ('수퍼', 8),
 ('하루시작', 7),
 ('소소한', 7),
 ('싶으', 7),
 ('디엠', 7),
 ('모닝채소', 7),
 ('올리브', 7),
 ('플랭크', 7),
 ('기다려', 7),
 ('짜고', 7),
 

 ('바꿨', 3),
 ('일과', 3),
 ('다시어터', 3),
 ('땡겼', 3),
 ('행복해', 3),
 ('소심식사', 3),
 ('힘찬', 3),
 ('빼기', 3),
 ('전자', 3),
 ('실험', 3),
 ('피쉬', 3),
 ('배고', 3),
 ('고맙다', 3),
 ('디저트그램', 3),
 ('소통스타그램', 3),
 ('생협', 3),
 ('아토', 3),
 ('학기', 3),
 ('말할', 3),
 ('사발', 3),
 ('볼일', 3),
 ('바지', 3),
 ('모에', 3),
 ('호가', 3),
 ('액체', 3),
 ('필요함', 3),
 ('맛있옹', 3),
 ('아웃', 3),
 ('발화', 3),
 ('이어지', 3),
 ('중요', 3),
 ('요하', 3),
 ('표현', 3),
 ('안다', 3),
 ('문장', 3),
 ('역할', 3),
 ('이해했', 3),
 ('이야기했', 3),
 ('다시한번', 3),
 ('육아일기', 3),
 ('감사할', 3),
 ('넘나맛난것', 3),
 ('소통그램', 3),
 ('핏콩큐브', 3),
 ('핏콩', 3),
 ('제이제이살롱드핏', 3),
 ('스파이', 3),
 ('망했', 3),
 ('미션오일', 3),
 ('스피커', 3),
 ('세심', 3),
 ('얼린', 3),
 ('무니', 3),
 ('무염', 3),
 ('인테이크lab', 3),
 ('씹힘', 3),
 ('맛있는한끼', 3),
 ('사라짐', 3),
 ('쌍콤', 3),
 ('예고', 3),
 ('극혐', 3),
 ('아이스초코', 3),
 ('과일스무디', 3),
 ('살빼는중', 3),
 ('동일', 3),
 ('참치쌈장', 3),
 ('망고젤리', 3),
 ('한시', 3),
 ('가공', 3),
 ('모자라', 3),
 ('가벼', 3),
 ('편할', 3),
 ('티비', 3),
 ('서나점심식단', 3),
 ('시작해', 3),
 ('유지어트', 3),
 ('날뻔', 3),
 ('유일하

 ('데일리포토', 2),
 ('일상기록�', 2),
 ('인형', 2),
 ('순두부찌개', 2),
 ('봄동', 2),
 ('와인안주', 2),
 ('좋아하지', 2),
 ('환절기', 2),
 ('나바코리아', 2),
 ('탕평채', 2),
 ('까까', 2),
 ('배부른바질씨드딸기', 2),
 ('화이트데이', 2),
 ('보상', 2),
 ('맞냐', 2),
 ('잇으', 2),
 ('시러', 2),
 ('머스탱v6', 2),
 ('솔직후기', 2),
 ('때매', 2),
 ('어쩔꺼야', 2),
 ('산달리기', 2),
 ('키로', 2),
 ('일교시', 2),
 ('내돈주고삼', 2),
 ('후쿠오카', 2),
 ('살빠진', 2),
 ('친구여', 2),
 ('까르', 2),
 ('와인', 2),
 ('타이밍', 2),
 ('생리', 2),
 ('증후군', 2),
 ('극한', 2),
 ('사투', 2),
 ('당하', 2),
 ('면하는', 2),
 ('배부른바질씨드바나나', 2),
 ('명품', 2),
 ('스팸마요덮밥', 2),
 ('여름맞이', 2),
 ('맛이다', 2),
 ('살뺄', 2),
 ('칼퇴', 2),
 ('비어포스트', 2),
 ('꼬냑', 2),
 ('김여우', 2),
 ('핫도그', 2),
 ('언스', 2),
 ('열려', 2),
 ('꺼내준', 2),
 ('지단', 2),
 ('시락', 2),
 ('이훈도시락', 2),
 ('웬만하면', 2),
 ('크런칩', 2),
 ('치킨와플', 2),
 ('아임웰굿밸런스도시락', 2),
 ('일상기록', 2),
 ('마이다노', 2),
 ('골뱅이', 2),
 ('된장찌개', 2),
 ('하장', 2),
 ('비스킷', 2),
 ('강타', 2),
 ('죽겠다', 2),
 ('응급실', 2),
 ('닫았', 2),
 ('콜라', 2),
 ('스파이스', 2),
 ('어떤맛', 2),
 ('살빼려', 2),
 ('거가', 2),
 ('영양소골고루', 2),
 ('꾸르맛', 

 ('순살', 1),
 ('불렀어욥', 1),
 ('데려가기', 1),
 ('장맛비', 1),
 ('매늬', 1),
 ('오십분', 1),
 ('메가마트', 1),
 ('메가마트온라인', 1),
 ('메가마트온라인쇼핑몰', 1),
 ('몸에좋은귀리', 1),
 ('남자한테참좋은데�', 1),
 ('좋드', 1),
 ('그만한', 1),
 ('쇼핑그램', 1),
 ('냠냠쩝쩝', 1),
 ('소통좋아요', 1),
 ('맞팔은댓', 1),
 ('한끼스타그램', 1),
 ('부족하더', 1),
 ('탄수화물중독', 1),
 ('간단한끼', 1),
 ('탄수화물대용', 1),
 ('길거리', 1),
 ('넘도', 1),
 ('허리휜', 1),
 ('3팩째', 1),
 ('눈물이뚝뚝', 1),
 ('둘째스타그램', 1),
 ('잘먹는아이', 1),
 ('아침엔다이어트', 1),
 ('제라일기', 1),
 ('물만두', 1),
 ('곤역', 1),
 ('약속했', 1),
 ('음층', 1),
 ('배꼽', 1),
 ('열찌', 1),
 ('절대로', 1),
 ('믹서기', 1),
 ('나죱', 1),
 ('나욥', 1),
 ('땅180625', 1),
 ('사몽', 1),
 ('뉴발란스양말득템', 1),
 ('첫도전', 1),
 ('도전스타그램', 1),
 ('써주시', 1),
 ('꾸벅', 1),
 ('토닥여', 1),
 ('기쁜', 1),
 ('모두수고하셨습니다�', 1),
 ('좋아하냐', 1),
 ('마카오커리', 1),
 ('섭렵', 1),
 ('인도', 1),
 ('커리덕후인증이벤트', 1),
 ('커리덕후_인테이크', 1),
 ('맛기행', 1),
 ('맛집리포터', 1),
 ('포커스', 1),
 ('넘기는', 1),
 ('펴져', 1),
 ('발린', 1),
 ('타지', 1),
 ('런타스틱', 1),
 ('흑석', 1),
 ('동작대교', 1),
 ('반포', 1),
 ('토요일아침', 1),
 ('6월23일', 1),
 ('잔잔', 1),
 ('열두

 ('씻은', 1),
 ('한칸띄우고', 1),
 ('닉스', 1),
 ('에어닉스', 1),
 ('메카닉일상', 1),
 ('질렀음', 1),
 ('쥬금', 1),
 ('날힘들게하는것들', 1),
 ('누릉', 1),
 ('끓이는', 1),
 ('두발', 1),
 ('출근하도', 1),
 ('맛은괜춤��', 1),
 ('서리태검은콩', 1),
 ('아프냐', 1),
 ('젭알', 1),
 ('안아', 1),
 ('푸게', 1),
 ('갱차', 1),
 ('차병원', 1),
 ('맛이쪄�', 1),
 ('착한칼로리', 1),
 ('두개는먹어야', 1),
 ('좀먹었다싶지', 1),
 ('더살찔듯', 1),
 ('좋아요반사감', 1),
 ('자그마한', 1),
 ('더살걸', 1),
 ('육아템', 1),
 ('쟁겨', 1),
 ('맛짱', 1),
 ('육아전쟁', 1),
 ('첫줄_', 1),
 ('첫줄�', 1),
 ('궁금함', 1),
 ('담백하다', 1),
 ('내통장털어서산간식', 1),
 ('서우부대찌개', 1),
 ('공지천닭갈비', 1),
 ('유통기한지남', 1),
 ('원하길', 1),
 ('먹으먄', 1),
 ('조정할', 1),
 ('돌아간', 1),
 ('유튜브', 1),
 ('정밀', 1),
 ('맛이쪄', 1),
 ('달달한아침', 1),
 ('또시킴', 1),
 ('바쁘게살기', 1),
 ('트와이닝얼그레이', 1),
 ('식사대용이라지만', 1),
 ('나에겐그냥배부른간식', 1),
 ('소셜을끊을수가없네', 1),
 ('운동에집중하자', 1),
 ('다이어트곤약젤리', 1),
 ('역시는역시', 1),
 ('아침아니고', 1),
 ('새로운맛이니', 1),
 ('다채롭', 1),
 ('근무시간', 1),
 ('보안씰', 1),
 ('보안', 1),
 ('닥더', 1),
 ('리브', 1),
 ('닥더리프', 1),
 ('수르지바', 1),
 ('채디디', 1),
 ('맛집블로거', 1),
 ('여행블로거채디디', 1),
 ('게

 ('접었', 1),
 ('뺑드미제빵소', 1),
 ('여친빵이랑', 1),
 ('잡담', 1),
 ('직접구매', 1),
 ('하이짐', 1),
 ('하이짐까치산점', 1),
 ('늦춰', 1),
 ('절차', 1),
 ('발표합', 1),
 ('올라가니', 1),
 ('트위터', 1),
 ('행운', 1),
 ('버터쿠키', 1),
 ('볼륨', 1),
 ('씹었', 1),
 ('먹으면서살빼기', 1),
 ('소소한일상', 1),
 ('조이사일상', 1),
 ('큰행복', 1),
 ('조언니소개템', 1),
 ('조언니추천템', 1),
 ('한봉지200칼로리', 1),
 ('진짜다이어트', 1),
 ('오일세퍼레이터', 1),
 ('머스탱인터쿨러', 1),
 ('영양실조', 1),
 ('나빠지는', 1),
 ('주며', 1),
 ('매곡동', 1),
 ('반월동', 1),
 ('부산시티투어', 1),
 ('아름다워', 1),
 ('막차', 1),
 ('밀떡', 1),
 ('모사금해변', 1),
 ('옥길동', 1),
 ('삼양검은모래해변', 1),
 ('고터', 1),
 ('수성구맛집', 1),
 ('신성동', 1),
 ('신지명사십리해변', 1),
 ('일광해수욕장', 1),
 ('팔공산카페', 1),
 ('대항해변', 1),
 ('상탑동', 1),
 ('서울살이', 1),
 ('패션그램', 1),
 ('책상밑비상식량', 1),
 ('텅장이되었다', 1),
 ('필요하', 1),
 ('해바', 1),
 ('티몬vvip', 1),
 ('티켓몬스터', 1),
 ('두돌', 1),
 ('열혈팬', 1),
 ('유전자', 1),
 ('아득아득', 1),
 ('히터바람', 1),
 ('눈꺼풀', 1),
 ('거려', 1),
 ('해야짘', 1),
 ('병정', 1),
 ('비자', 1),
 ('워커홀릭', 1),
 ('기뻐해', 1),
 ('뒤엎', 1),
 ('구축', 1),
 ('주7일근무', 1),
 ('등대', 1),
 ('퇴근할때가장기쁨', 1),
 ('

 ('심곡동', 1),
 ('힙스터', 1),
 ('내추럴플랜', 1),
 ('몸값', 1),
 ('주치의', 1),
 ('감성마력', 1),
 ('조촐하', 1),
 ('잘해야', 1),
 ('압력', 1),
 ('크류', 1),
 ('엑셀', 1),
 ('광고모델', 1),
 ('짧지', 1),
 ('살균', 1),
 ('콜레스', 1),
 ('음용', 1),
 ('알레르기', 1),
 ('내지', 1),
 ('소린', 1),
 ('겠거', 1),
 ('로선', 1),
 ('믹싱하', 1),
 ('선팔후맞팔', 1),
 ('광고지', 1),
 ('노골', 1),
 ('제약', 1),
 ('올려놓', 1),
 ('목포', 1),
 ('보스니아헤르체고비나', 1),
 ('단발', 1),
 ('고을', 1),
 ('보라매', 1),
 ('lchf식단', 1),
 ('아라모드', 1),
 ('피임법', 1),
 ('완료기', 1),
 ('한솔동', 1),
 ('미인계', 1),
 ('약선도시락', 1),
 ('분당홈페이지제작', 1),
 ('물산', 1),
 ('용산', 1),
 ('조르', 1),
 ('마니시', 1),
 ('성일', 1),
 ('디지털', 1),
 ('타워', 1),
 ('협성대', 1),
 ('금영', 1),
 ('노래방', 1),
 ('기기', 1),
 ('맥포', 1),
 ('방촌', 1),
 ('브리딩', 1),
 ('사천진해변', 1),
 ('녹동', 1),
 ('방재', 1),
 ('항맥', 1),
 ('외과', 1),
 ('산업', 1),
 ('반월당역', 1),
 ('구로동', 1),
 ('유성', 1),
 ('감속', 1),
 ('삼호', 1),
 ('불가사리', 1),
 ('워드프레스', 1),
 ('사이버', 1),
 ('일육삼오', 1),
 ('피스', 1),
 ('지례', 1),
 ('오류동역', 1),
 ('원주제이투', 1),
 ('논현로', 1),
 ('명태', 1),
 ('회무침', 1),
 ('간병인', 1),


 ('다음엔오리지널로', 1),
 ('미래엔', 1),
 ('한입거리', 1),
 ('생각보다맛있다', 1),
 ('씨씨앙체험단신청', 1),
 ('꺄앙', 1),
 ('비타민구미좋다', 1),
 ('뽑아줘요', 1),
 ('딱딱하네', 1),
 ('장땡', 1),
 ('지루', 1),
 ('지나가', 1),
 ('아임리얼클렌징', 1),
 ('필수식단', 1),
 ('두개먹었지롱', 1),
 ('출근샷', 1),
 ('불필요하다', 1),
 ('지켜보겠', 1),
 ('3주체험', 1),
 ('치면', 1),
 ('하루5끼', 1),
 ('반하고', 1),
 ('허해', 1),
 ('먹어주고', 1),
 ('소원', 1),
 ('우리애들밥상', 1),
 ('베이비라이브tv', 1),
 ('요리왕', 1),
 ('아기밥', 1),
 ('아기시럽', 1),
 ('소키', 1),
 ('홈쿠킹', 1),
 ('2시간만에다시공복', 1),
 ('409일차', 1),
 ('예방접종', 1),
 ('측정', 1),
 ('내려가지', 1),
 ('꾸준함이답이다�', 1),
 ('픽셀', 1),
 ('플라잉디스크', 1),
 ('수제견과류바', 1),
 ('퇴근하겠습니다', 1),
 ('잘먹을께요', 1),
 ('피웠', 1),
 ('돌보기', 1),
 ('보련', 1),
 ('가져다줬', 1),
 ('내사랑쿠팡맨�', 1),
 ('서른셋', 1),
 ('삼삼한곽원장', 1),
 ('컨디션제로', 1),
 ('뽁뽁', 1),
 ('졍이_받았다그램', 1),
 ('맞다', 1),
 ('자랑하고', 1),
 ('곳도', 1),
 ('집착', 1),
 ('훈스타그램', 1),
 ('티볼리에어', 1),
 ('가솔린', 1),
 ('개월전', 1),
 ('계획해', 1),
 ('착하네', 1),
 ('하루끝_꿈', 1),
 ('홀더', 1),
 ('마블', 1),
 ('마시멜로우', 1),
 ('건조과일', 1),
 ('홀가분나이트마켓', 1),
 ('88잔디마당', 1),
 ('

 ('시빅', 1),
 ('버나비', 1),
 ('복장', 1)]


In [13]:
labnosh.nav_merged = labnosh.merge_list(labnosh.nav_list)
labnosh.nav_frequency = frequency(labnosh.nav_merged)
print(labnosh.nav_frequency [:5])

[('랩노쉬', 10886), ('다이어트', 2730), ('맛', 1694), ('미래형식사', 1628), ('올리브영', 1355)]


## 여기서 내가 형태소분석시에 안짤리게 할 단어와 제외하고 싶은 단어, 대체하고 싶은 단어를 선택한다.
## 안짤리게 할 단어는 다시 위로 돌아가 추가한다.
## 대체하고 싶은 단어와 제외하고 싶은 단어는 아래 방법으로 처리한다. 일단 생략한다.

## 분석에서 제외할 단어를 리스트로 넣어준다. 인자로 넣어주는 값은 변하지 않으므로 넣어보고 마음에 안들면 다시 intake.nav_list 로 접근하면 삭제 전 파일로 돌아갈 수 있다.
## 진짜 후회없을 것 같을 때, intake.nav_list에 업데이트 하도록 하자.

In [ ]:
intake.nav_frequency = frequency(intake.nav_merged)

In [ ]:
intake.nav_frequency [:5]

In [ ]:
modified_nav_list = intake.word_delete(intake.nav_list, ['요거', '여러', '굳이'])
print(modified_nav_list[0])

## 이번에는 단어를 대체하는 것, 리스트 안에 딕셔너리 형식
#### [{'main': '최종적으로 대체하고 싶은 단어', 'sub_words':['대체할 단어', '대체할 단어']},
####  {'main': '최종적으로 대체하고 싶은 단어', 'sub_words':['대체할 단어', '대체할 단어']}]

In [ ]:
modified_nav_list_2 = intake.word_substitute(modified_nav_list, [{'main':'모닝죽', 'sub_words':['단호박', '단호박이', '꿀고구마']}])
print(modified_nav_list_2[0])

### 토픽모델링은 조인된 것이 필요하다.
### join_list 를 통해서 만들기

In [26]:
intake.morph_joined = intake.join_list(intake.nav_list)

In [27]:
labnosh.morph_joined = labnosh.join_list(labnosh.nav_list)

AttributeError: 'Social_analysis' object has no attribute 'nav_list'

### 파라미터는 다음과 같다. 
#### self.make_lda(self, morph_joined, ntopic=10, learning_method='batch', max_iter=25, random_state=0, n_words=20)
#### ntopic과 n_words를 넣어주면 몇개의 토픽으로 나눌지, 몇개의 단어를 보여줄지를 정할 수 있다.

In [28]:
intake.LDA = SB_LDA()
intake.LDA.make_lda(intake.morph_joined, ntopic=10)

topic 0       topic 1       topic 2       topic 3       topic 4       
--------      --------      --------      --------      --------      
모닝죽           힘내            있는            다이어트          건강            
아침            운동            많은            저녁            다이어트          
일상            시켜            입니            다이어터          구매            
먹스타그램         않아            있어            점심            먹스타그램         
다이어트          먹겠            같아            들어오시          맛스타그램         
단호박           타서            이벤트           다이어트그램        링크            
간식            주문했           씨씨앙           1개            데일리           
고구마           않는            아니            먹고            유산균           
데일리           씹어            괜찮            받은            건강식           
맛스타그램         드시            없는            사과            후기            
소통            찍어            있다            함께하는          선물            
단호박죽          정모            참여            고구마           간식            
식단조절  

In [ ]:
labnosh.LDA = SB_LDA()
labnosh.LDA.make_lda(labnosh.morph_joined, ntopic=10)

### 그 토픽과 관련된 문서 10개를 보여준다. 두번째 인자는 토픽의 인덱스이고 세번째 인덱스는 보여줄 포스팅의 개수이다.

In [ ]:
topic0 = intake.LDA.related_doc(intake.modified[:,2], 0, 4)

In [ ]:
topic0 = labnosh.LDA.related_doc(labnosh.raw_data[:,2], 0, 4)

### 데이터 형식은 같고 할 줄 알겠지?

In [ ]:
intake.SB_word2vec = SB_Word2Vec(intake.nav_list)

intake.flavor = intake.SB_word2vec.get_sim_sen('맛', intake.modified[:,2], 4)

In [ ]:
labnosh.SB_word2vec = SB_Word2Vec(labnosh.nav_list)

labnosh.flavor = labnosh.SB_word2vec.get_sim_sen('맛', labnosh.raw_data[:,2], 4)

In [21]:
intake.SB_word2vec.em.wv.most_similar('맛') 

[('맛은', 0.6681041717529297),
 ('식감', 0.6280479431152344),
 ('생각보다', 0.6160725355148315),
 ('새콤달콤', 0.6123064756393433),
 ('미숫가루', 0.5867149829864502),
 ('단맛', 0.5775174498558044),
 ('단점', 0.5737367868423462),
 ('고소', 0.5660829544067383),
 ('조금', 0.5660343170166016),
 ('약간', 0.5656855702400208)]

most_similar(positive=None, negative=None, topn=10, restrict_vocab=None, indexer=None)¶

model.wv.most_similar(positive=['woman', 'king'], negative=['man'])
[('queen', 0.50882536), ...]

model.wv.most_similar_cosmul(positive=['woman', 'king'], negative=['man'])
[('queen', 0.71382287), ...]


model.wv.doesnt_match("breakfast cereal dinner lunch".split())
'cereal'

In [22]:
intake.SB_word2vec.em.wv.most_similar(positive=['아침', '맛'], negative=['운동'])

[('미숫가루', 0.5826406478881836),
 ('생각보다', 0.579865574836731),
 ('심지어', 0.5629949569702148),
 ('귀리', 0.5474948883056641),
 ('완전', 0.5468454957008362),
 ('아주', 0.5345592498779297),
 ('맛나', 0.5310249328613281),
 ('그냥', 0.5308135747909546),
 ('일단', 0.5180487036705017),
 ('좋아', 0.5167618989944458)]

## TFIDF에는 merge 된 리스트를 넣어서 비교해주면 된다. 
## intake만 있어서 패스
## 토픽모델링 된 애들끼리 비교해보는 것도 좋을 듯.

In [23]:
tfidf = SB_Tfidf([intake.nav_merged, labnosh.nav_merged])
tfidf.get_tfidf()
tfidf_of_all = tfidf.tfidf_hangul

for i in tfidf_of_all:
    pprint(i[:10])
    print()

[('흡기', 0.25419146503600865),
 ('튜닝', 0.23128150466795636),
 ('좋은', 0.2160081977559215),
 ('파워젤부스트', 0.18764348491928534),
 ('카스타그램', 0.1800068314632679),
 ('자동차', 0.17346112850096726),
 ('아미노리커버', 0.1680063760323834),
 ('먹으면', 0.16364257405751628),
 ('단팥죽', 0.13418691072716335),
 ('머플러', 0.13091405924601301)]

[('으로', 0.4224923468565074),
 ('쇼콜라', 0.34686938659387423),
 ('미식당', 0.3169824681667258),
 ('많이', 0.22822737708004256),
 ('맛이', 0.19471780187384585),
 ('그래놀라요거트', 0.18384983153670095),
 ('자색고구마', 0.18203850314717682),
 ('푸드쉐이크', 0.17162336490741298),
 ('그린씨리얼', 0.16664221183622158),
 ('함께', 0.13856662179859727)]



## 디비로 넣어보자.

In [12]:
converted_array = intake.convert_list(intake.nav_list, intake.noun_list, intake.verb_list, intake.adj_list)

list index out of range 끝


In [13]:
converted_array[:2, :]

array([['아침식사/죽/모닝/죽/단호박/테이크/먹는/모닝/죽/아침/바쁘/기도/하고/입맛/없는/요거/하나/아침/뚝딱/맛/여러/종류/있는/맛있는/굳이/고르/단호박/새로/나온/고구마/맛있',
        '아침식사/죽/모닝/죽/단호박/테이크/모닝/죽/아침/기도/입맛/요거/하나/아침/뚝딱/맛/여러/종류/굳이/단호박/고구마',
        '바쁘/없는/있는/맛있는/새로/맛있', '먹는/하고/고르/나온'],
       ['바쁜/아침/식사/대용/마시/있는/가벼운/테이크/밀스/라이트/간편하게/있고/영양소/까지/챙길/있어/밀스/라이트/덕분/아침/거르/없어/아침/마다/포만/운동하는/직장인/식단/인증/하루/시작/간식/타임/아침/스타/그램/간식/식사/대용/건강/스타/그램/건강/그램/식사/아침식사/아침/스타/그램/맛있다/그램/맛스타/그램',
        '아침/식사/대용/테이크/밀스/라이트/영양소/까지/밀스/라이트/덕분/아침/거르/아침/마다/포만/직장인/식단/인증/하루/시작/간식/타임/아침/스타/그램/간식/식사/대용/건강/스타/그램/건강/그램/식사/아침식사/아침/스타/그램/그램/맛스타/그램',
        '바쁜/있는/가벼운/간편하게/있고/있어/없어/맛있다', '마시/챙길/운동하는']], dtype='<U1206')

In [14]:
df = intake.make_df(converted_array)

In [15]:
df.haed

AttributeError: 'DataFrame' object has no attribute 'haed'

In [ ]:
len(intake.nav_list)

In [ ]:
df = pd.DataFrame(np.hstack((intake.modified[:,:3], converted_array, intake.modified[:, 3:])), index=None)
# 소정이가 전체 tag 포함된 것 join해주는 것 추가해주면
# df = pd.DataFrame(np.hstack((intake.modified[:,:3], morph_list, converted_array, intake.modified[:, 3:])), index=None, columns=[])
# 이걸로 하면 된다.

In [16]:
df.head(10)

0                         1   \
0      lora.study  2018-07-03T23:57:47.000Z   
1        1122_asm  2018-07-02T01:08:57.000Z   
2     makemysugar  2018-07-05T13:13:05.000Z   
3   oasis_jaeyoon  2018-06-28T01:59:52.000Z   
4        khjhmom_  2018-07-04T11:01:04.000Z   
5        leeminwk  2018-06-12T11:05:21.000Z   
6           vveun  2018-06-13T13:26:21.000Z   
7    _si1ver_star  2018-01-14T12:30:54.000Z   
8  kyu_ri_the_one  2018-04-21T12:56:13.000Z   
9    untactmarket  2018-07-06T07:46:02.000Z   

                                                  2   \
0  lora.study 아침식사 죽 모닝죽 단호박 인테이크\n.\n몇년째 먹는 모닝죽\...   
1  1122_asm.\n바쁜아침 식사대용으로 마시고 있는,\n가벼운 한끼  인테이크  ...   
2  makemysugar.\n아침에 귀찮아서 간편하게 귀리우유 한 잔�!\n고소~~하니...   
3  oasis_jaeyoon오늘 아침은 짜먹는 죽. 어제 모임에서 선물로 받았다. 세상...   
4  khjhmom_몸을 좀비워야할시기�\n.\n.\n.\n 육아한답시고 너무먹어ㅎ ㅎ\...   
5  leeminwk차에서 라디오 듣다 문자 보냈는데  인테이크 상품권 받음.\n요즘은 ...   
6                                vveun나이제 술 안먹어�� 정말   
7  _si1ver_star1일1식으로 딱이야 넘 맛남( ๑॔˃̶◡ ˂̶๑॓)◞♡\n 인...   
8  kyu_ri_the_one고소하고 맛있는 175kal 한 끼 식사�\n.\n.\n....   
9  untactmarket-\n지금 샐러드를 사면\n럭키 복권이 따라와요!\n긁으면 대...   

                                                  3   \
0  아침식사/죽/모닝/죽/단호박/테이크/먹는/모닝/죽/아침/바쁘/기도/하고/입맛/없는/...   
1  바쁜/아침/식사/대용/마시/있는/가벼운/테이크/밀스/라이트/간편하게/있고/영양소/까...   
2  아침/귀찮/간편하게/귀리/우유/고소/하니/미숫가루/먹는/텐바이텐/텐텐/쇼퍼/텐텐/쇼...   
3                    오늘/아침/먹는/죽/어제/모임/선물/받았/세상/변해/간다   
4                     몸/좀비/야할/육아/답시고/너무/먹어/테이크/모닝/귀리   
5       라디오/듣다/문자/보냈/테이크/상품권/요즘/정말/간편식/세상/소소하지/확실/자랑   
6                                           나이/먹어/정말   
7                                 맛남/테이크/죽/모닝/죽/다이어트   
8       고소하고/맛있는/식사/테이크/테이크/푸드/카페라떼/벨벳/초콜렛/맛/식사/다이어트   
9  지금/샐러드/사면/럭키/복권/따라와/긁으/대박/애플/워치/식사/시간/박스/인바디/체...   

                                                  4   \
0  아침식사/죽/모닝/죽/단호박/테이크/모닝/죽/아침/기도/입맛/요거/하나/아침/뚝딱/...   
1  아침/식사/대용/테이크/밀스/라이트/영양소/까지/밀스/라이트/덕분/아침/거르/아침/...   
2  아침/귀리/우유/고소/하니/미숫가루/텐바이텐/텐텐/쇼퍼/텐텐/쇼퍼/테이크/귀리/오트...   
3                             오늘/아침/죽/어제/모임/선물/세상/간다   
4                           몸/좀비/육아/답시고/너무/테이크/모닝/귀리   
5                  라디오/문자/테이크/상품권/요즘/정말/간편식/세상/확실/자랑   
6                                              나이/정말   
7                                 맛남/테이크/죽/모닝/죽/다이어트   
8                식사/테이크/테이크/푸드/카페라떼/벨벳/초콜렛/맛/식사/다이어트   
9  지금/샐러드/사면/럭키/복권/대박/애플/워치/식사/시간/박스/인바디/체중/초과/경품...   

                            5                      6   \
0           바쁘/없는/있는/맛있는/새로/맛있            먹는/하고/고르/나온   
1  바쁜/있는/가벼운/간편하게/있고/있어/없어/맛있다             마시/챙길/운동하는   
2                      귀찮/간편하게                     먹는   
3                           변해                  먹는/받았   
4                           야할                     먹어   
5                         소소하지                  듣다/보냈   
6                                                  먹어   
7                                                       
8                     고소하고/맛있는                          
9                               따라와/긁으/부담해야/하며/따른/요청할   

                                                  7   \
0  아침식사/죽/모닝죽/단호박/인테이크/맛스타그램/lfl/foodporn/먹스타그램/식...   
1  인테이크/밀스라이트/운동하는직장인/식단인증/하루시작/간식타임/아침스타그램/간식/식사...   
2  텐바이텐/텐텐쇼퍼/텐텐쇼퍼3기/인테이크/귀리/오트밀/모닝귀리/귀리우유/일상/oats...   
3  인테이크/모닝죽/위워크/weworkkr/gracemlee/soylavender/oa...   
4  육아한답시고/너무먹어ㅎ/인테이크/모닝귀리/khjhmom_/artheart_centr...   
5                                           인테이크/간편식   
6  인테이크/인테이크밀스/미스터네이처/도시락/금주/lovelyuluv/choi.seun...   
7                     인테이크/죽/모닝죽/다이어트/ouo_0i/99_0425   
8  intakefoods/인테이크/인테이크푸드/카페라떼/벨벳초콜렛/맛/한끼/식사/다이어...   
9  언택트마켓/샐러드자판기/이색자판기/먹스타그램/직장인스타그램/점심메뉴/아침밥/샐러드/...   

                                                  8      9   \
0  lora.study#맛스타그램#lfl#foodporn#먹스타그램#식사대용#다이어트#...    163   
1                                                     2,540   
2                                                        25   
3  oasis_jaeyoon#인테이크 #모닝죽 #위워크 #weworkkr/graceml...     42   
4  jj_hummi요거 좋습니까??/khjhmom_일단 맛은 괜찮아요 ㅎ 근데 계속뭐가...          
5  ddk3096우아ㅡㅋㅋㅋ당첨./yih

## 이 데이터 프레임을 넣어주면 될듯

array([['lora.study', '2018-07-03T23:57:47.000Z',
        'lora.study 아침식사 죽 모닝죽 단호박 인테이크\n.\n몇년째 먹는 모닝죽\n아침엔 바쁘기도 하고 입맛도 없는데 요거하나면 아침뚝딱�\n맛은 여러종류가 있는데.. 다 맛있는데 굳이 고르자면 단호박이랑 새로 나온 꿀고구마가 맛있오�',
        '아침식사/죽/모닝죽/단호박/인테이크/모닝죽/아침/기도/입맛/요거/하나/아침/뚝딱/맛은/여러/종류/맛있는데/굳이/단호박이/꿀고구마',
        '바쁘/없는/있는/새로/맛있', '고르/나온',
        '아침식사/죽/모닝죽/단호박/인테이크/맛스타그램/lfl/foodporn/먹스타그램/식사대용/다이어트/두통/좋아요반사/instant/맛집/간편식/아점/fff/아픔/선팔은맞팔/맛스타/선팔/fastfood/맞팔/meal/먹스타/음식/푸드스타그램/brunch/좋반',
        'lora.study#맛스타그램#lfl#foodporn#먹스타그램#식사대용#다이어트#두통#좋아요반사#instant#맛집#간편식#아점#fff#아픔#선팔은맞팔#맛스타#선팔#fastfood#맞팔#meal#먹스타#음식#푸드스타그램#brunch#좋반/orado912선팔눌렀어요~/pty119멋지네요😺/jobodas좋아요 꾹 클릭하고 갈께요~ ^^',
        '163',
        'https://www.instagram.com/p/Bkye0hsFHJB/?hl=ko&tagged=%EC%9D%B8%ED%85%8C%EC%9D%B4%ED%81%AC'],
       ['1122_asm', '2018-07-02T01:08:57.000Z',
        '1122_asm.\n바쁜아침 식사대용으로 마시고 있는,\n가벼운 한끼  인테이크  밀스라이트\n.\n간편하게 먹을 수 있고 영양소까지 챙길 수 있어요!\n밀스라이트 덕분에 아침 거르는 일 없어요.\n아침마다 포만감있게 호로록!\n.\n.\n.\n.\n.\n 운동하는직장인  식단인증  하

In [49]:
converted_array.shape

(5235, 3)

In [1]:
labnosh = Social_analysis('labnosh.txt', 'labnosh.official')

meals = Social_analysis('meals.txt', 'intakefoods')

morningjuk = Social_analysis('morningjuk.txt', 'intakefoods')

easy_food = Social_analysis('easy_food.txt')

conven_food = Social_analysis('conven_food.txt')

keywords = [intake, labnosh, meals, morningjuk, easy_food, conven_food]

### 빈도분석

for i in keywords:
    print(len(i.main_text_list), len(i.morph_merged))

labnosh.morph_frequency = analyzer.frequency(labnosh.morph_merged)
pprint(labnosh.morph_frequency)

meals.morph_frequency = analyzer.frequency(meals.morph_merged)
pprint(meals.morph_frequency)

morningjuk.morph_frequency = analyzer.frequency(morningjuk.morph_merged)
pprint(morningjuk.morph_frequency)

easy_food.morph_frequency = analyzer.frequency(easy_food.morph_merged)
pprint(easy_food.morph_frequency)

conven_food.morph_frequency = analyzer.frequency(conven_food.morph_merged)
pprint(conven_food.morph_frequency)

### 토픽모델링

intake.LDA = analyzer.SB_LDA()
intake.LDA.make_lda(intake.morph_joined, ntopic=10)

topic0 = intake.LDA.related_doc(intake.main_text_list, 0)

topic1 = intake.LDA.related_doc(intake.main_text_list, 1)

topic2 = intake.LDA.related_doc(intake.main_text_list, 2)

topic3 = intake.LDA.related_doc(intake.main_text_list, 3)

topic7 = intake.LDA.related_doc(intake.main_text_list, 7)

topic9 = intake.LDA.related_doc(intake.main_text_list, 9)

topic3 = intake.LDA.related_doc(intake.main_text_list, 3)



labnosh.LDA = analyzer.SB_LDA()
labnosh.LDA.make_lda(labnosh.morph_joined, ntopic=10)

meals.LDA = analyzer.SB_LDA()
meals.LDA.make_lda(meals.morph_joined, ntopic=10)

morningjuk.LDA = analyzer.SB_LDA()
morningjuk.LDA.make_lda(morningjuk.morph_joined, ntopic=10)

easy_food.LDA = analyzer.SB_LDA()
easy_food.LDA.make_lda(easy_food.morph_joined, ntopic=10)

conven_food.LDA = analyzer.SB_LDA()
conven_food.LDA.make_lda(conven_food.morph_joined, ntopic=10)

### Word2Vec

intake.SB_word2vec = analyzer.SB_Word2Vec(intake.hashtags_appended)

intake.flavor = intake.SB_word2vec.get_sim_sen('맛', intake.main_hash_dic, intake.main_text_list, 4)


intake.diet = intake.SB_word2vec.get_sim_sen('다이어트', intake.main_hash_dic, intake.main_text_list, 4)


intake.health = intake.SB_word2vec.get_sim_sen('건강', intake.main_hash_dic, intake.main_text_list, 4)


intake.exercise = intake.SB_word2vec.get_sim_sen('운동', intake.main_hash_dic, intake.main_text_list, 4)


intake.morningjuk = intake.SB_word2vec.get_sim_sen('모닝죽', intake.main_hash_dic, intake.main_text_list, 4)


intake.meals = intake.SB_word2vec.get_sim_sen('밀스', intake.main_hash_dic, intake.main_text_list, 4)


intake.gonyak = intake.SB_word2vec.get_sim_sen('곤약젤리', intake.main_hash_dic, intake.main_text_list, 4)




### TFIDF

tfidf = analyzer.SB_Tfidf([intake.morph_merged, labnosh.morph_merged, meals.morph_merged, morningjuk.morph_merged, easy_food.morph_merged, conven_food.morph_merged])

tfidf_of_all = tfidf.tfidf_hangul

for i in tfidf_of_all:
    pprint(i[:10])
    print()

meals_juk_SB_Tfidf = analyzer.SB_Tfidf([meals.morph_merged, morningjuk.morph_merged])

tfidf_meals_juk = meals_juk_SB_Tfidf.tfidf_hangul

for i in tfidf_meals_juk:
    pprint(i[:10])
    print()

intake_meals_SB_Tfidf = analyzer.SB_Tfidf([intake.morph_merged, meals.morph_merged])

tfidf_intake_meals = intake_meals_SB_Tfidf.tfidf_hangul

for i in tfidf_intake_meals:
    pprint(i[:10])
    print()

intake_morningjuk_SB_Tfidf = analyzer.SB_Tfidf([intake.morph_merged, morningjuk.morph_merged])

tfidf_intake_morningjuk = intake_morningjuk_SB_Tfidf.tfidf_hangul

for i in tfidf_intake_morningjuk:
    pprint(i[:10])
    print()

meals_conven_food_SB_Tfidf = analyzer.SB_Tfidf([meals.morph_merged, conven_food.morph_merged])

tfidf_meals_conven_food = meals_conven_food_SB_Tfidf.tfidf_hangul

for i in tfidf_meals_conven_food:
    pprint(i[:10])
    print()

morningjuk_conven_food_SB_Tfidf = analyzer.SB_Tfidf([morningjuk.morph_merged, conven_food.morph_merged])

tfidf_morningjuk_conven_food = morningjuk_conven_food_SB_Tfidf.tfidf_hangul

for i in tfidf_meals_conven_food:
    pprint(i[:10])
    print()

C:\Users\abys\Anaconda3\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


In [9]:
import csv
with open('morph_list.csv', 'w', encoding='utf-8') as f:
    spamwriter = csv.writer(f, delimiter=' ',
                            quotechar='|', quoting=csv.QUOTE_MINIMAL)
    for i in intake.morph_list:
        spamwriter.writerow(i)

In [16]:
def morph_pos(text_list, add_list, del_list, exception_list = ['맛', '밥', '물', '몸']):
    morph_list = []
    noun_list = []
    adj_list = []
    verb_list = []

    for j in text_list:
        parsed = self.twitter.pos(j)
        temp = []
        n_temp = []
        adj_temp = []
        verb_temp = []

        for i in parsed:
            if self.isHangul(i):
                if not i[0] in del_list:
                    if len(i[0]) > 1:
                        temp.append(i)
                        if i[1] == 'Noun':
                            n_temp.append(i[0])
                        elif i[1] == 'Verb':
                            n_adj.append(i[0])
                        elif i[1] == 'Adjective':
                            n_verb.append(i[0])

                    elif i in exception_list:
                        temp.append(i)
            else: print(i, '한글이 아닙니다.')

        morph_list.append(temp)
        noun_list.append(n_temp)
        adj_list.append(adj_temp)
        verb_list.append(verb_temp)


    nav_list = noun_list + adj_list + verb_list

    return morph_list, nav_list, noun_list, adj_list, verb_list

In [ ]:

    '''def get_from_dic(self, filename):
        self.data = handler.load_by_pickle(filename)
        self.dataset, self.dataset_dic, self.main_text_list, self.morph_list, self.morph_merged, self.morph_joined, self.hashtags_merged, self.hashtags_appended, self.main_hash_dic = handler.create_datasets_with_dic(self.data)

        # dataset, main_text_list, morph_list, morph_merged, morph_joined, hashtags_merged, hashtags_appended, main_hash_dic
    def get_data_from_list(self, filename, add_list, del_list):
        self.data = handler.load_by_pickle(filename)
        self.dataset, self.main_text_list, self.morph_list, self.morph_merged, self.morph_joined, self.hashtags_merged, self.hashtags_appended, self.main_hash_dic = handler.create_datasets_with_list(self.data[1:], add_list, del_list)'''
